# Drawing and running simple missions

## Overview

Aviary comes with a simple built-in graphical interface for defining missions.
This tool can be accessed via the command line and provides an interactive way to define flight phases, including altitude, Mach number, and optimization parameters.

It is specifically made to only be used with the `"height_energy"` mission method.
You could use the results from the GUI to run a mission with a different method, but it would require manually changing the generated `phase_info` python dictionary.

![Graphical user interface for drawing missions](images/gui_main.png)

In [ ]:
# Testing Cell
from aviary.interface.utils.check_phase_info import check_phase_info, HEIGHT_ENERGY
check_phase_info({}, HEIGHT_ENERGY)

## Getting Started

To launch the Flight Profile Utility, use the following command in your terminal:

```bash
aviary draw_mission
```

This command will open a graphical interface where you can interactively design a flight profile.

In [ ]:
# Test Cell
from aviary.interface.cmd_entry_points import _command_map
_command_map['draw_mission'];

```{note}
If you are [WSL on Windows](https://learn.microsoft.com/en-us/windows/wsl/install) you might need to install an [X Server](https://sourceforge.net/projects/xming/) to run the GUI without issues. If you do this, also modify your `.bashrc` file to include this line: `export DISPLAY=localhost:0.0`. 
```

## Graphical Interface Usage

### Main Components

1. **Altitude Profile**: Graphically represents the altitude profile over time. Users can add new points by clicking on the plot and edit existing points by dragging. Units and axes limits can be changed through the menu.

2. **Mach Profile**: Similar to the Altitude Plot but for the Mach number profile.

3. **Table Entry**: Tabular form of defining a mission. You can add new points through the `Add New Point` button, edit existing points by changing the values in the table entries, and delete points by pressing the `X` button next to any point. The plots and tables update with changes to either one.

### Interactive Features

- **Adding Points**: Click on either the Altitude or Mach plot area to add a new point. Points on the Altitude plot represent altitude (in feet by default) at a specific time (in minutes by default), whereas points on the Mach plot represent the Mach number at specific times.

- **Dragging Points**: Points on both plots can be dragged to adjust values. This allows for fine-tuning of the flight profile.

- **Removing Points**: Press the `X` button next to the point on the tabular section to remove that point.

- **Output Phase Info**: Press this button to create an output python file named `outputted_phase_info.py` which contains the mission information in a python dictionary called `phase_info`. This button serves the same function as using the menu <nobr>`File`->`Save`</nobr> command. 

- **Light/Dark Mode**: Press the button on the bottom left to toggle the theme between light and dark mode. The default is light mode. If the user chooses to save settings (read `Edit Tab` below), the last used theme will be loaded the next time the program is run.

### Menu Options
#### File Tab
1. **Open Phase Info**: Allows user to open a previously made phase info file. This must be a python file that contains a dictionary called `phase_info`. 

2. **Save Phase Info**: Peforms the same function as clicking on the `Output Phase Info` button by saving the current mission as a phase info dictionary in a file named `outputted_phase_info.py`.

3. **Save Phase Info as**: Save the current mission as a phase info dictionary with the filename and location specified by the user.

4. **Exit**: Close the program.

#### Edit Tab
1. **Axes Limits**: Lets the user change the axes limits for the Altitude and Mach plots. Pressing the reset button will change the axes limits to be able to view all the points.

2. **Units**: Lets the user change the units for Time and Altitude. The default units are minutes and feet respectively.<br>
***Currently supported units:***<br>
Time: seconds (s), minutes (min), hours (h)<br>
Altitude: meters (m), kilometers (km), feet (ft), miles (mi), nautical miles (nmi)

3. **Rounding**: Lets the user change the rounding options for Time, Altitude, and Mach. The number corresponds to the number of digits after the decimal point. 

4. **Store Settings?**: Toggle the option to store settings. The program can store the user's last used theme (dark/light mode) and the last used screen size and location. If this option is checked, the next time the program is run it will open with the same theme and window size and location as the previous use. Unchecking this option will remove any files that store settings.

#### View Tab
1. **Optimize Phase**: Toggle the option to show/hide optimization checkboxes. If checked, the user can choose to optimize altitude and/or mach for each phase of the mission. Checking the option will create checkboxes between each point on the tabular section of the program.

2. **Phase Slopes**: Toggle the option to show/hide slopes for each mission phase. If checked, the altitude and mach plots will be populated with text that shows the climb rate (altitude/time) and mach rate (mach/time). The units for these values will use the same units as the plots. The slope values are rounded to two more digits than the point values.  

3. **Advanced Options**: Shows a dialog box for editing more settings for the mission.<br>
3.1. `Constrain Range`: If checked, imposes constraints on the flight range.<br>
3.2. `Solve for Distance`: If checked, calculates the total flight range based on the profile.<br>
3.3. `Include Takeoff`: If checked, includes takeoff in the mission analysis.<br>
3.4. `Include Landing`: If checked, includes landing in the mission analysis.<br>
3.5. `Polynomial Control Order`: Sets the polynomial order for control optimization, default being 1. This is for all phases. You can modify behavior on a per-phase basis by editing the outputted `phase_info` dict.<br>
3.6. `Phase Transcription Order`: This setting will only show once at least 2 points are added to the plots/table. This number controls the number of points that are used to evaluate each mission phase. The minimum value is 3, and increasing this value will increase the number of points Aviary uses to analyze that phase.

#### Help Tab
1. **Instructions**: Shows instructions on how to use the program.

### Output

Upon completion, the tool outputs a Python script named `outputted_phase_info.py` in the current working directory. Alternatively, if the user uses the `Save As` command, a python script with the user specified name will be saved in the user specified directory. This tool overwrites any existing python file with the same name as the output. This outputted file contains the `phase_info` dictionary, which holds the flight profile data structured for use in mission simulations.

```{note}
When using the outputted `phase_info` dict in a mission simulation, you can modify the settings by directly changing the outputted Python file.
```

The `phase_info` dictionary makes some assumptions about different settings which you can also modify.
For example, the time duration of each phase is controlled by the optimizer if `fix_duration` is False, though this can be changed to True to fix the duration of each phase.

If you don't have the [black](https://pypi.org/project/black/) python autoformatter installed, your output may look slightly different - as long as you see confirmation that your phase info has been saved, your mission profile was successfully created.

## Running a Mission Simulation

After generating the flight profile, use the `run_mission` command to simulate the mission.
This command utilizes the `phase_info` from `outputted_phase_info.py` and simulates the mission based on the defined parameters. In the commands below, replace `outputted_phase_info.py` with your filename if you choose to save the output file with a different filename.
You can use the `--phase_info` flag to specify the path to the `outputted_phase_info.py` file.
Here we use a benchmark case as the inputted .csv file, though you can use any Aviary .csv here that defines an aircraft.

```bash
aviary run_mission --phase_info outputted_phase_info.py validation_cases/benchmark_tests/test_aircraft/aircraft_for_bench_FwFm.csv
```

You can also supply an optimizer, otherwise the default (SLSQP) will be used.
Here is how you'd run the mission with the IPOPT optimizer:

```bash
aviary run_mission --optimizer IPOPT --phase_info outputted_phase_info.py validation_cases/benchmark_tests/test_aircraft/aircraft_for_bench_FwFm.csv
```

```{note}
When you run Aviary all of the outputs will be saved in the location where you run the command or run script.
Outputs files such as optimization history and Dymos output files are saved at that location.
A folder named 'report' will also be created there, and contains all of the associated report files for your runs.
These reports include [optimization and trajectory reports generated by OpenMDAO and Dymos](https://openmdao.org/newdocs/versions/latest/features/reports/reports_system.html).
```

In [ ]:
# Testing Cell
from aviary.docs.tests.utils import run_command_no_file_error
command = 'aviary run_mission --optimizer IPOPT --phase_info outputted_phase_info.py '\
    'validation_cases/benchmark_tests/test_aircraft/aircraft_for_bench_FwFm.csv'
command += ' --max_iter 0'
run_command_no_file_error(command)